In [1]:
# console and directory access
import os
import re
import datetime

# interacting with Amazon AWS
import boto3
from sagemaker.session import Session

# data reading and exporting  
import json
import pandas as pd
import numpy as np

# parsing SEC website for data  
import requests 
from bs4 import BeautifulSoup

## Archived Dealer Data Import from 1993
Parses in dealer information with accompaning CIK code for EDGAR lookup from the SEC dealer registration

In [2]:
def companyName(cik:str) -> str:
    """
    Returns the company name for a given CIK number from the SEC by parsing 
    the Edgar site for current company name filing
    
    Input:
        :param: cik (type str)
            The CIK number for a broker dealer e.g. 887767
    Return:
        :param: (type str)
            Returns the accompanying name with the CIK provided 
            e.g. 1ST GLOBAL CAPITAL CORP. 
    """
    
    # establishing base-url for company name search
    baseURL = 'https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&'
    current_year = datetime.datetime.today().year
    url = baseURL+'CIK={}&type=X-17A-5&dateb={}1231'.format(cik, current_year)
    
    # response time for retrieving company names, returning beautifulsoup obj.
    res = requests.get(url, allow_redirects=True)
    s1 = BeautifulSoup(res.text, 'html.parser')
    
    # select the company information from the SEC website for a particular CIK
    for val in s1.find_all('span', attrs={"class":"companyName"}):
        
        # retrieve the company name from info class
        comp_name = val.text.split('CIK')[0].split('/BD')[0]
        print('\t\tFound CIK {}, company-name {}'.format(cik, comp_name))
        
        return comp_name

In [3]:
def dealerData(years:list, quarters:list=['QTR1', 'QTR2', 'QTR3', 'QTR4'], 
               cik2brokers:dict={'years-covered':[], 'broker-dealers':{}}) -> dict:
    """
    Retrieve dealer data from archived SEC directory, returns a dictionary of essential information
    
    Input:
        :param: years (type list)
            A list of years to check for additional dealer data to be pulled e.g. [1993, 1994, 2000]. NOTE, that
            only the years specified are checked for dealer information. 
        :param: quarters (type list)
            A list of quarters to check for additional dealer data, string must be of the form "QTRX", where X is 
            an integer from 1-4 inclusive default = [QTR1, QTR2, QTR3, QTR4]. 
        :param: cik2brokers (type dictionary)
            A nested dictionary for storing the broker-dealer data as well as the years covered from the archive 
            e.g. {'years-reported':['2020/QTR1', '2020/QTR2'],'broker-dealers':{1904: 'ABRAHAM SECURITIES CORPORATION'}}. 
    Return:
        :param: cik2brokers (type dict)
            Returns a dictionary with CIK:CompanyName relationships e.g. {887767: 1ST GLOBAL CAPITAL CORP.} as well 
            as metadata on how many years and quarters were retrieved last
    """
    
    # archived data website for broker dealer data
    baseURL = 'https://www.sec.gov/Archives/edgar/full-index'
    
    # extract all the years covered from json form (we want to avoid re-runs) 
    archiveDates = ['{}/{}'.format(yt, qt) for yt in years for qt in quarters]
    years_covered = cik2brokers['years-covered']
    
    # itterate through years and quarters for archival search
    for coverage in archiveDates:

        if coverage in years_covered:
            print('\tWe have covered {}'.format(coverage))
            pass

        else:
            searchURL = '{}/{}/form.idx'.format(baseURL, coverage)
            print('\nSearching for broker dealers at {}'.format(searchURL))

            # send request to SEC website to retrieve broker dealer information 
            response = requests.get(searchURL, allow_redirects=True)

            # if reponse type is active we return object with status code 200 (else error)
            if response.status_code == 200:

                # append the coverage year for the cik in question
                cik2brokers['years-covered'].append(coverage)

                # extract only main text from body, selecting terms below dashes '---' 
                # we use triple dashes to avoid improper splits that exist locally with company names
                data = response.text.split('---')[-1]   

                # write contents to a temporary file to read information
                with open('main.txt', 'w') as file: file.write(data)

                # convert text data to dataframe object using a fixed-width-file convention
                df = pd.read_fwf('main.txt', header=None)
                cleanDf = df[~pd.isnull(df[0])]               # strip away rows with NaN from the Form Type column

                # check to see if first column contains information on X-17A-5 filings (use regex for x-17a flag)
                x17_check = cleanDf[0].str.contains('^x-17a', regex=True, flags=re.IGNORECASE)
                x17File = cleanDf[x17_check]

                print('\tFound {} X-17A-5 filings in {}'.format(x17File.shape[0], coverage))

                # check whether X-17A-5 form type was found (if empty pass)
                if not x17File.empty:

                    # CIK number is taken from the last column of the rows splitting url string by row 
                    # e.g. edgar/data/886475/0001019056-10-000046.txt -> 886475
                    last_column = x17File.columns[-1]
                    cikNumbers = x17File[last_column].apply(lambda x: x.split('/')[2]).values
                    
                    # compute dictionary mapping for the CIK and company name for each broker-dealer    
                    dictionary_update = dict(map(lambda x: (x, companyName(x)), cikNumbers))

                    # update the broker-dealer list
                    cik2brokers['broker-dealers'].update(dictionary_update)

                # remove local file after it has been created
                os.remove('main.txt')
        
    return cik2brokers

In [ ]:
if __name__ == "__main__":
    
    # s3 active folder for outputs
    bucket = "ran-s3-systemic-risk"
    folder ="Temp/"

    # Amazon Textract client and Sagemaker session
    s3 = boto3.client('s3')
    session = Session()

    paths = session.list_s3_files(bucket, folder)
    
    # determine the interval range for which we look back historically 
    parse_years = np.arange(1993, datetime.datetime.today().year+1)

    # if the CIK-Dealer file is located in the output folder we read it in and pass as argument
    if 'Temp/CIKandDealers.json' in paths: 
        # retrieving downloaded files from s3 bucket
        s3.download_file(bucket, 'Temp/CIKandDealers.json', 'temp.json')
        
        # read all CIK and Dealer name information from storage
        with open('temp.json', 'r') as f: old_cik2brokers = json.loads(f.read())
            
        cik2brokers = dealerData(years=parse_years, cik2brokers=old_cik2brokers)   
        
        # remove local file after it has been created
        os.remove('temp.json')
    else:
        # otherwise we must run the entire history of broker-dealers registering a X-17A-5 file
        cik2brokers = dealerData(years=parse_years)
        
    # write to a JSON file with accompanying meta information about coverage 
    with open('CIKandDealers.json', 'w') as file:
        json.dump(cik2brokers, file)
        file.close()
    
    # save contents to AWS S3 bucket
    with open('CIKandDealers.json', 'rb') as data:
        s3.upload_fileobj(data, bucket, 'Temp/CIKandDealers.json')
        
    # remove local file after it has been created
    os.remove('CIKandDealers.json')
    

	We have covered 1993/QTR1
	We have covered 1993/QTR2
	We have covered 1993/QTR3
	We have covered 1993/QTR4
	We have covered 1994/QTR1
	We have covered 1994/QTR2
	We have covered 1994/QTR3
	We have covered 1994/QTR4
	We have covered 1995/QTR1
	We have covered 1995/QTR2
	We have covered 1995/QTR3
	We have covered 1995/QTR4
	We have covered 1996/QTR1
	We have covered 1996/QTR2
	We have covered 1996/QTR3
	We have covered 1996/QTR4
	We have covered 1997/QTR1
	We have covered 1997/QTR2
	We have covered 1997/QTR3
	We have covered 1997/QTR4
	We have covered 1998/QTR1
	We have covered 1998/QTR2
	We have covered 1998/QTR3
	We have covered 1998/QTR4
	We have covered 1999/QTR1
	We have covered 1999/QTR2
	We have covered 1999/QTR3
	We have covered 1999/QTR4
	We have covered 2000/QTR1
	We have covered 2000/QTR2
	We have covered 2000/QTR3
	We have covered 2000/QTR4

Searching for broker dealers at https://www.sec.gov/Archives/edgar/full-index/2001/QTR1/form.idx
	Found 2 X-17A-5 filings in 2001/QTR1


		Found CIK 1071638, company-name AURORA SECURITIES INC 
		Found CIK 1084325, company-name ALBANY SECURITIES, LLC. 
		Found CIK 715628, company-name STATESIDE SECURITIES, LLC 
		Found CIK 922070, company-name ALERUS SECURITIES CORPORATION 
		Found CIK 1055902, company-name ALETHEIA SECURITIES, INC., 
		Found CIK 867629, company-name ALEX MOORE & COMPANY, INC. 
		Found CIK 1005744, company-name ALEXANDER CAPITAL, L.P. 
		Found CIK 757015, company-name DON ALEXANDER INVESTMENTS, INC. 
		Found CIK 842984, company-name ALEXANDER DUNHAM SECURITIES, INC. 
		Found CIK 842986, company-name ALEXANDER GABOR & CO, INC. 
		Found CIK 911591, company-name ALFS, INC. 
		Found CIK 3588, company-name ALL FUNDS, INC. 
		Found CIK 701520, company-name ALL-VEST SECURITIES, INC. 
		Found CIK 892896, company-name ALLAPREE SECURITIES, INC. 
		Found CIK 1127577, company-name ALLEGIANCE CAPITAL, L.L.C. 
		Found CIK 3683, company-name ALLEN & COMPANY LLC 
		Found CIK 200014, company-name ALLEN & COMPANY OF FLOR

		Found CIK 352296, company-name APS FINANCIAL CORPORATION 
		Found CIK 932340, company-name ARAGON INVESTMENTS, LTD. 
		Found CIK 1054453, company-name ARAPAHO PARTNERS, LLC 
		Found CIK 824662, company-name ARBOR RESEARCH & TRADING, LLC 
		Found CIK 914855, company-name ARBORHEDGE INVESTMENTS, INC. 
		Found CIK 932530, company-name ARCADIA INVESTMENT CORPORATION 
		Found CIK 1053731, company-name ARCADIA SECURITIES, LLC 
		Found CIK 1038165, company-name ARCHELON LLC 
		Found CIK 1071637, company-name ARCHON SECURITIES, LLC 
		Found CIK 1139505, company-name ARCLIGHT FINANCIAL LLC                                  
		Found CIK 1005814, company-name ARGENT CLASSIC CONVERTIBLE ARBITRAGE FUND L.P. 
		Found CIK 857155, company-name ARGENT INVESTMENT SERVICES, INC. 
		Found CIK 215131, company-name ARGUS SECURITIES, INC. 
		Found CIK 944360, company-name ARIEL DISTRIBUTORS, LLC 
		Found CIK 1138684, company-name ARISTATRADE SECURITIES, LLC 
		Found CIK 1041846, company-name ARISTEIA TRADIN

		Found CIK 845013, company-name OHANESIAN / LECOURS, INC. 
		Found CIK 890383, company-name BANORTE-IXE SECURITIES INTERNATIONAL, LTD. 
		Found CIK 1067122, company-name KIPPSDESANTO & COMPANY 
		Found CIK 832719, company-name BANYAN SECURITIES, LLC 
		Found CIK 9874, company-name BARCLAY INVESTMENTS LLC 
		Found CIK 851376, company-name BARCLAYS CAPITAL INC. 
		Found CIK 1002197, company-name BLACKROCK EXECUTION SERVICES 
		Found CIK 882676, company-name BARING INVESTMENT SERVICES, INC. 
		Found CIK 880915, company-name BARINGTON CAPITAL GROUP, L.P. 
		Found CIK 887602, company-name BARRETT & COMPANY, INC. 
		Found CIK 1087945, company-name BARRETT SECURITIES INC. 
		Found CIK 1001371, company-name BARRIGER & BARRIGER INCORPORATED 
		Found CIK 857294, company-name BARRINGTON ASSOCIATES 
		Found CIK 887084, company-name NANCY BARRON & ASSOCIATES, INC. 
		Found CIK 1085799, company-name RIVIERE SECURITIES LTD. 
		Found CIK 802617, company-name BARTON HALL SECURITIES, INC. 
		Found CIK 

		Found CIK 886078, company-name BNP PARIBAS BROKERAGE SERVICES, INC. 
		Found CIK 1052943, company-name BNP PARIBAS INVESTMENT SERVICES, LLC 
		Found CIK 753835, company-name BNP PARIBAS SECURITIES CORP. 
		Found CIK 796559, company-name BNY ASSOCIATES INCORPORATED 
		Found CIK 755925, company-name BNY CLEARING SERVICES LLC 
		Found CIK 917380, company-name COWEN EXECUTION SERVICES LLC 
		Found CIK 1088945, company-name BNY INVESTMENT CENTER INC. 
		Found CIK 1018264, company-name BNY TRADING LLC 
		Found CIK 12933, company-name BOENNING & SCATTERGOOD, INC. 
		Found CIK 700332, company-name BOLTON FINANCIAL SERVICES, LLC 
		Found CIK 1119810, company-name BOND EXPRESS, INC. 
		Found CIK 1103218, company-name TRADEWEB DIRECT LLC 
		Found CIK 1113381, company-name BONDHUB, INC. 
		Found CIK 1095240, company-name BONDNET BROKERS INC                                     
		Found CIK 1137614, company-name BONDS DIRECT SECURITIES LLC 
		Found CIK 1140711, company-name BONDWAVE LLC 
		Found C

...

		Found CIK 1082960, company-name MILESTONE INVESTMENTS, INC. 
		Found CIK 1449651, company-name MILLBURN RIDGEFIELD CORPORATION 
		Found CIK 1469553, company-name MILLENNIUM ADVISORS, LLC 
		Found CIK 1116109, company-name MILLER BUCKFIRE & CO., LLC 
		Found CIK 1434780, company-name MILLINGTON SECURITIES, INC. 
		Found CIK 719188, company-name MINT BROKERS 
		Found CIK 890203, company-name MIRAE ASSET SECURITIES (USA) INC. 
		Found CIK 1440241, company-name MIRAE ASSET WEALTH MANAGEMENT (USA) INC. 
		Found CIK 1321919, company-name MITCHELL ENERGY ADVISORS, LLC 
		Found CIK 1422725, company-name MIURA CAPITAL, LLC 
		Found CIK 1145897, company-name MKM PARTNERS LLC 
		Found CIK 1049767, company-name MMA SECURITIES LLC 
		Found CIK 1105818, company-name MMC SECURITIES LLC 
		Found CIK 943903, company-name MML DISTRIBUTORS, LLC 
		Found CIK 701059, company-name MML INVESTORS SERVICES, LLC 
		Found CIK 1582604, company-name MML STRATEGIC DISTRIBUTORS, LLC 
		Found CIK 1683785, company-n

		Found CIK 1515901, company-name PEAKSTONE SECURITIES, LLC 
		Found CIK 1420524, company-name PENSERRA SECURITIES, LLC 
		Found CIK 1007500, company-name PENTALPHA CAPITAL, LLC 
		Found CIK 861941, company-name PENTEGRA DISTRIBUTORS INC. 
		Found CIK 719538, company-name PEOPLE'S SECURITIES, INC. 
		Found CIK 1345290, company-name PERELLA WEINBERG PARTNERS LP 
		Found CIK 920788, company-name PERFORMANCE TRUST CAPITAL PARTNERS, LLC 
		Found CIK 926544, company-name PERSHING ADVISOR SOLUTIONS LLC 
		Found CIK 29648, company-name PERSHING LLC 
		Found CIK 1290271, company-name PETRIE PARTNERS SECURITIES, LLC 
		Found CIK 354497, company-name PFS INVESTMENTS INC. 
		Found CIK 1440313, company-name PHARUS SECURITIES, LLC 
		Found CIK 1650211, company-name PHILOSMITH SECURITIES LLC 
		Found CIK 1280139, company-name PICKWICK CAPITAL PARTNERS, LLC 
		Found CIK 1385551, company-name PINNACLE INVESTMENTS, LLC (SUCCESSOR) 
		Found CIK 870866, company-name PJ SOLOMON SECURITIES, LLC 
		Found CI

		Found CIK 1564913, company-name SENAHILL SECURITIES, LLC 
		Found CIK 1427708, company-name SENDERO SECURITIES, LLC 
		Found CIK 1007086, company-name SENTINEL BROKERS COMPANY, INC. 
		Found CIK 1565380, company-name SEPULVEDA DISTRIBUTORS LLC 
		Found CIK 1303465, company-name SEQUENCE FINANCIAL SPECIALISTS LLC 
		Found CIK 1002134, company-name SEQUOIA INVESTMENTS, INC. 
		Found CIK 1670331, company-name SERA GLOBAL SECURITIES US LLC 
		Found CIK 1399880, company-name SEVEN POINTS CAPITAL, LLC 
		Found CIK 1166315, company-name SFG SECURITIES, INC. 
		Found CIK 1261467, company-name SG AMERICAS SECURITIES, LLC 
		Found CIK 1462624, company-name SHANNON ADVISORS LLC 
		Found CIK 1468209, company-name SHARENETT SECURITIES LLC 
		Found CIK 1467855, company-name SHEA & COMPANY, LLC 
		Found CIK 945520, company-name SHEARSON FINANCIAL SERVICES, LLC 
		Found CIK 1513552, company-name SHELTER ROCK CAPITAL GROUP LLC 
		Found CIK 1504259, company-name SHERMAN & COMPANY LLC 
		Found CIK 9009

		Found CIK 1497950, company-name TIGRESS FINANCIAL PARTNERS, LLC 
		Found CIK 709480, company-name TIMBER HILL LLC 
		Found CIK 1748185, company-name TIMBREL CAPITAL, LLC 
		Found CIK 1145266, company-name TIME EQUITIES SECURITIES LLC 
		Found CIK 1223025, company-name TITLEIST ASSET MANAGEMENT, LTD. 
		Found CIK 1072769, company-name TJM INVESTMENTS, LLC 
		Found CIK 1461130, company-name TNCP, LLC 
		Found CIK 1670449, company-name TOPCAP PARTNERS, INC. 
		Found CIK 1325845, company-name TORA TRADING SERVICES, LLC 
		Found CIK 1530262, company-name TORCH PARTNERS CORPORATE FINANCE INC 
		Found CIK 1706134, company-name TORREYA CAPITAL, LLC 
		Found CIK 1686088, company-name TORTOISEECOFIN SECURITIES, LLC 
		Found CIK 1503998, company-name TOWERBROOK FINANCIAL, L.P. 
		Found CIK 1103218, company-name TRADEWEB DIRECT LLC 
		Found CIK 1034262, company-name TRADEWEB L.L.C 
		Found CIK 1127272, company-name TRADIER BROKERAGE, INC. 
		Found CIK 872796, company-name TRADITION SECURITIES AN

		Found CIK 1223205, company-name X-CHANGE FINANCIAL ACCESS, LLC 
		Found CIK 1420989, company-name XML SECURITIES, LLC 
		Found CIK 1513209, company-name XP INVESTMENTS US, LLC 
		Found CIK 1413732, company-name XR SECURITIES LLC 
		Found CIK 1146299, company-name XT CAPITAL PARTNERS, LLC 
		Found CIK 1715650, company-name XTX MARKETS LLC 
		Found CIK 1659056, company-name YUKI-CO, LLC 
		Found CIK 1086916, company-name ZERMATT SECURITIES, INC. 
		Found CIK 795051, company-name ZEUS FINANCIAL, LLC 
		Found CIK 790482, company-name ZIONS DIRECT, INC. 
		Found CIK 881810, company-name AKIN BAY COMPANY LLC 
		Found CIK 856380, company-name ALLIANZ GLOBAL INVESTORS DISTRIBUTORS LLC 
		Found CIK 1144526, company-name ANKURA CAPITAL ADVISORS, LLC 
		Found CIK 1683672, company-name ANNEXUS SECURITIES, LLC 
		Found CIK 1683672, company-name ANNEXUS SECURITIES, LLC 
		Found CIK 1025038, company-name ARVEST INVESTMENTS, INC. 
		Found CIK 865838, company-name BBVA SECURITIES INC. 
		Found CIK 17